$\newcommand\N{\mathbb N}
\newcommand\llbracket{[\![}
\newcommand\rrbracket{]\!]}
\newcommand\bbr[2]{\llbracket #1,#2\rrbracket}
\newcommand\stirlingb[2]{\left\lbrace{#1}\atop{#2}\right\rbrace}$

# Nombres de Bell et nombres de Stirling

Marc Lorenzi

3 mai 2025

In [ ]:
import matplotlib.pyplot as plt

## 1. Partitions et nombres de Bell

### 1.1 Partitions

Une *partition* de l'ensemble $E$ est un ensemble $P$ de parties de $E$ vérifiant

- Pour tout $A$ appartenant à $P$, $A\ne\emptyset$
- Pour tous $A$, $B$ distincts appartenant à $P$, $A\cap B=\emptyset$
- Pour tous $a\in E$, il existe $A\in P$ (nécessairement unique) tel que $a\in A$.

On note $\Pi(E)$ l'ensemble des partitions de $E$.

La fonction `partitions` énumère les partitions d'un ensemble fini $E$, donné par la liste de ses éléments. Le principe de la fonction est le suivant. Si $E=\emptyset$, $E$ a une unique partition, l'ensemble vide. Sinon, soit $a\in E$. Toute partition $P\in\Pi(E)$ s'écrit alors de façon unique $P=\{A\cup\{a\}\}\cup P'$ où $A\in\mathcal P(E\setminus\{a\})$ et $P'\in\Pi(E\setminus A)$.

In [ ]:
def partitions(E):
    if E == []: yield []
    else:
        a = E[0]
        E1 = E[1:]
        for A in parties(E1):
            E2 = sub(E1, A)
            for P1 in partitions(E2):
                P = [[a] + A] + P1
                yield P

In [ ]:
def parties(E):
    if E == []: yield []
    else:
        a = E[0]
        E1 = E[1:]
        for P1 in parties(E1):
            yield P1
            yield [a] + P1

In [ ]:
for A in parties([1,2,3]):
    print(A, end=' ')

In [ ]:
def sub(A, B):
    return [a for a in A if a not in B]

In [ ]:
sub([1,2,3,4,5], [2,4])

In [ ]:
k = 1
for P in partitions([1, 2, 3, 4]):
    print(k, P)
    k = k + 1

### 1.2 Nombres de Bell

Si $E$ est un ensemble fini de cardinal $n$, le cardinal de $\Pi(E)$ ne dépend que de $n$ et pas de $E$. On note $B_n$ ce cardinal. Les entiers $B_n$ sont les *nombres de Bell*. Voici une première version très inefficace du calcul de $B_n$. Cette fonction compte les partitions de $E$, où $E$ est de cardinal $n$.

In [ ]:
def bell1(n):
    k = 0
    E = list(range(n))
    for P in partitions(E):
        k += 1
    return k

In [ ]:
for n in range(11):
    print(n, bell1(n))

### 1.2 Une relation sur les nombres de Bell

Reprenons l'idée de la foncion `partitions`. Soit $n\in\N$. Soit $E$ un ensemble fini de cardinal $n+1$. Soit $a\in E$. Pour toute partition $P$ de $E$, notons $A_P$ l'élément de $P$ qui contient $a$. Considérons la fonction $\Phi$ définie par $\Phi(P)=(A_P\setminus\{a\}, P\setminus\{A_P\})$. L'ensemble de départ de $\Phi$ est $\Pi(E)$. Son ensemble d'arrivée est

$$F=\bigcup_{A\in\mathcal P(E\setminus\{a\})}\{A\}\times\Pi(E\setminus (A\cup\{a\}))$$

La fonction $\Phi$ est bijective. Sa réciproque est la fonction $\Psi:F\longrightarrow\Pi(E)$ définie par

$$\Psi(A,P')=\{A\cup\{a\}\}\cup P'$$

Réécrivons $F$ en regraoupant par ensembles $A$ de même cardinal :

$$F=\bigcup_{k=0}^n\bigcup_{A\in\mathcal P_k(E\setminus\{a\})}\{A\}\times\Pi(E\setminus (A\cup\{a\}))$$

Comme l'union qui définit $F$ est disjointe,

\begin{eqnarray*}
|F|&=&\sum_{k=0}^n\sum_{A\in\mathcal P_k(E\setminus\{a\})}|\{A\}|\times|\Pi(E\setminus (A\cup\{a\}))|\\
&=&\sum_{k=0}^n\sum_{A\in\mathcal P_k(E\setminus\{a\})}B_{n-k}\\
&=&\sum_{k=0}^n\binom n kB_{n-k}
\end{eqnarray*}

En posant $j=n+1-k$ dans la somme ci-dessus, on obtient

$$B_{n+1}=\sum_{j=0}^{n}\binom n{n-j}B_{j}$$

ou encore, par symétrie des coefficients binomiaux,

$$B_{n+1}=\sum_{j=0}^{n}\binom njB_{j}$$

Sachant que $B_0=1$, nous avons donc une relation de récurrence sur les nombres de Bell.

La fonction `liste_bell` renvoie la liste $[B_0,\ldots,B_N]$. Avant la $n$ième itération de la boucle `for`, la liste `cbs` contient les coefficients binomiaux $\binom {n-1}0$, ...,$\binom {n-1}{n-1}$. La liste `bs` contient $B_0,\ldots,B_{n-1}$.

In [ ]:
def liste_bell(N):
    cbs = [1]
    bs = [1]
    for n in range(1, N + 1):
        b = 0
        for k in range(n):
            b += cbs[k] * bs[k]
        bs.append(b)
        cbs1 = (n + 1) * [0]
        cbs1[0] = 1
        for k in range(1, n):
            cbs1[k] = cbs[k - 1] + cbs[k]
        cbs1[n] = 1
        cbs = cbs1
    return bs

In [ ]:
def bell(n):
    return liste_bell(n)[n]

In [ ]:
bs = liste_bell(10)
for n in range(11):
    print(n, bs[n])

Nous pouvons maintenant calculer sans problème le millième nombre de Bell.

In [ ]:
print(bell(1000))

## 2. Nombres de Stirling de deuxième espèce

### 2.1 Partitions de cardinal fixé

Soient $p\in\N$. Pour tout ensemble $E$, notons $\Pi_p(E)$ l'ensemble des partitions de $E$ de cardinal $p$. Si $E$ est fini, de cardinal $n$, le cardinal de $\Pi_p(E)$ ne dépend que de $n$ et $p$, et pas de $E$. On note $\stirlingb n p$ ce cardinal. Les entiers $\stirlingb n p$ sont les *nombres de Stirling de deuxième espèce*.

La fonction `partitions2` énumère les partitions de $\Pi_p(E)$, où $E$ est un ensemble fini. L'idée est la suivante. Si $E$ est vide, c'est immédiat. Sinon, soit $a\in E$. Soit $E'=E\setminus\{a\}$. On a 

$$\Pi_p(E)=\Pi'_p(E)\cup\Pi''_p(E)$$

où

- $\Pi'_p(E)$ est l'ensemble des partitions $P\in\Pi_p(E)$ telles que $\{a\}\in P$.
- $\Pi''_p(E)$ est l'ensemble des partitions $P\in\Pi_p(E)$ telles que $\{a\}\not\in P$.

On a

$$\Pi'_p(E)=\{P\cup\{a\}:P\in\Pi_{p-1}(E')\}$$

et

$$\Pi''_p(E)=\bigcup_{P\in\Pi_p(E')}\hat P$$

où $\hat P$ est l'ensemble des $p$ parttions de $E$ obtenues en ajoutant $a$ à l'un des éléments de la partition $P$.

In [ ]:
def partitions2(E, p):
    if E == []: 
        if p == 0: yield []
        else: pass
    else:
        a = E[0]
        E1 = E[1:]
        for P in partitions2(E1, p - 1):
            yield [[a]] + P
        for P in partitions2(E1, p):
            for k in range(p):
                yield P[:k] + [[a] + P[k]] + P[k+1:]

In [ ]:
for P in partitions2([1,2,3,4], 3): print(P)

La fonction `stirling2` renvoie inefficacement $\stirlingb n p$, en comptant les éléments de $\Pi_p(E)$, où $E$ est un ensemble fini de cardinal $n$.

In [ ]:
def stirling1(n, p):
    E = list(range(n))
    k = 0
    for P in partitions2(E, p):
        k += 1
    return k

In [ ]:
for n in range(11):
    for p in range(11):
        print('%6d' % stirling1(n, p), end='')
    print()

### 2.2 Une relation de récurrence sur les nombres de Stirling

Soient $n,p\in\N^*$. Soit $E$ un ensemble fini de cardinal $n$. Soit $a\in E$ fixé. Posons $E'=E\setminus\{a\}$. Reprenons les idées du paragraphe 2.1. On a

$$|\Pi'_p(E)|=|\Pi_{p-1}(E')|=\stirlingb{n-1}{p-1}$$

et

$$|\Pi''_p(E)|=p|\Pi_{p}(E')|=p\stirlingb{n-1}{p}$$

De là, par union disjointe,

$$\stirlingb{n}{p}=\stirlingb{n-1}{p-1}+p\stirlingb{n-1}{p}$$

La fonction `liste_stirling` renvoie la liste des $\stirlingb Np$ pour $p\in\bbr0N$.

In [ ]:
def liste_stirling(N):
    ss = (N + 1) * [0]
    ss[0] = 1
    for n in range(1, N + 1):
        ss1 = (N + 1) * [0]
        for p in range(1, n + 1):
            ss1[p] = ss[p - 1] + p * ss[p]
        ss = ss1
    return ss

In [ ]:
for n in range(11):
    ss = liste_stirling(n)
    for p in range(n + 1):
        print('%6d' % ss[p], end='')
    print()

In [ ]:
def stirling(n, p):
    return liste_stirling(n)[p]

In [ ]:
print(stirling(939, 393))

In [ ]:
plt.rcParams['figure.figsize'] = (8, 3)

In [ ]:
n = 100
xs = range(1, n + 1)
ys = liste_stirling(n)[1:]
plt.semilogy(xs, ys, 'k', lw=1, base=10)
plt.grid()